In [1]:
# Copyright 2024 Keysight Technologies Inc.

In [2]:
import trueq as tq
import numpy as np
import trueq.compilation as tqc
from trueq.config import fsim_factory
from trueq import CircuitCollection

cycle1 = {1: tq.Gate.h, 4: tq.Gate.h}
cycle2 = {(0, 1): tq.Gate.random(4)}
cycle3 = {1: tq.Gate.t, 3: tq.Gate.random(2)}
cycle4 = tq.Cycle({(1, 3): fsim_factory(11, 13)})

circuit = tq.Circuit([cycle1, cycle2, cycle3, cycle4] * 2)
circuit += cycle1
circuit.measure_all()
circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [3]:
rc_circuits = tq.randomly_compile(circuit, entangler=tq.Gate.cx)
rc_circuits[0].draw()

DisplayWrapper(<svg xmlns="http://w...)

In [4]:
def rc_kak(circuit, n_compilations=30, local=True):
    circuits = CircuitCollection(circuit.__copy__() for _ in range(n_compilations))
    passes = [
        tqc.MarkCycles(),  # mark any cycles with two-qubit gates
        tqc.RCKak(local=local),  # apply randomizing cycles around marked cycles
        tqc.Merge(),
        tqc.RemoveEmptyCycle(),
    ]
    return tqc.Compiler(passes).compile(circuits)

In [5]:
kak_rc_circuits = rc_kak(circuit, n_compilations=30, local=True)
kak_rc_circuits[0].draw()

DisplayWrapper(<svg xmlns="http://w...)

In [6]:
rc_kak(circuit, n_compilations=30, local=False)[0].draw()

DisplayWrapper(<svg xmlns="http://w...)

In [7]:
# use an ideal simulator to obtain the ideal output distribution
sim = tq.Simulator()
ideal_result = sim.sample(circuit, n_shots=np.inf)

# create a noisy simulator to observe the output in the presence of overrotation noise
noisy_sim = tq.Simulator().add_overrotation(single_sys=0.01, multi_sys=0.1)
noisy_result = noisy_sim.sample(circuit, n_shots=np.inf)

# estimate the ideal distribution using the collection of circuits obtained from RCKak
kak_rc_result = sum(
    noisy_sim.sample(kak_circuit, n_shots=np.inf) for kak_circuit in kak_rc_circuits
)

# likewise using the collection of circuits obtained from RC with an additional
# decomposition step
rc_result = sum(
    noisy_sim.sample(rc_circuit, n_shots=np.inf) for rc_circuit in rc_circuits
)

# compare the total variation distance between the estimated distributions and the ideal
bare_tvd = noisy_result.tvd(ideal_result)
kak_rc_tvd = kak_rc_result.normalized().tvd(ideal_result)
rc_tvd = rc_result.normalized().tvd(ideal_result)

print("TOTAL VARIATION DISTANCE")
print("Noisy simulation without RC: {:.4f}".format(bare_tvd[0]))
print("Noisy simulation with RCKak: {:.4f}".format(kak_rc_tvd[0]))
print("Noisy simulation with RC (using entangler): {:.4f}".format(rc_tvd[0]))

TOTAL VARIATION DISTANCE
Noisy simulation without RC: inf
Noisy simulation with RCKak: 0.0557
Noisy simulation with RC (using entangler): inf


         (/home/jenkins/workspace/release trueq/trueq/results.py:489)
         (/home/jenkins/workspace/release trueq/trueq/results.py:489)


In [8]:
circuit = tq.Circuit({(0, 1): tq.Gate.from_generators("YY", 45)})
circuit.measure_all()
circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [9]:
kak_rc_circuits = rc_kak(circuit, n_compilations=30, local=True)

# obtain the ideal output distribution
ideal_result = sim.sample(circuit, n_shots=np.inf)

# simulate with overrotation noise
noisy_sim = tq.Simulator().add_overrotation(multi_sys=0.1)
noisy_result = noisy_sim.sample(circuit, n_shots=np.inf)

# estimate using RCKak
kak_rc_result = sum(
    noisy_sim.sample(kak_circuit, n_shots=np.inf) for kak_circuit in kak_rc_circuits
)

# compare the total variation distance
bare_tvd = noisy_result.tvd(ideal_result)
kak_rc_tvd = kak_rc_result.normalized().tvd(ideal_result)

print("TOTAL VARIATION DISTANCE")
print("Noisy simulation without RC: {:.4f}".format(bare_tvd[0]))
print("Noisy simulation with RCKak: {:.4f}".format(kak_rc_tvd[0]))

TOTAL VARIATION DISTANCE
Noisy simulation without RC: 0.0288
Noisy simulation with RCKak: 0.0288


In [10]:
tq.settings.set_dim(3)

# Apply RCKak to a cycle containing two-qutrit gates
qutrit_rc_circuits = rc_kak(
    tq.Circuit({(0, 1): tq.Gate.random(9), (2, 3): tq.Gate.cx3}),
    n_compilations=30,
    local=True,
)
qutrit_rc_circuits[0].draw()

DisplayWrapper(<svg xmlns="http://w...)